# Analysis of Foul Trouble Player Effectiveness

By: Erin Neaton

## Introduction
A common, yet difficult decision in basketball is whether to sit a player when they are in foul trouble. When players are in foul trouble, coaches have to balance missing out on a player's effectiveness and difference making on the court with risking the player getting more fouls and ultimately fouling out. In this project, I aim to compare the effectiveness of players while in and not in foul trouble. This analysis includes traditional statistics such as shooting percentage and rebounds. It also includes a new angle of analysis- how these elements are impacted by the player's distance from opposing players. I examine whether there are significant changes in a player's distance to other players on the court when they are in foul trouble versus when they are not. This would be an indication that the player is playing less aggressively, so this method will measure effectiveness that isn't captured by traditional statistics. This information would assist coaches in making informed decisions under pressure of when to sit a player and when to leave them in the game, based on their expected effectiveness.

## Purpose & Motivation


In [1]:
# Import packages.
import pandas as pd
import numpy as np
import json
import math
import warnings

In [2]:
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)

In [3]:
warnings.filterwarnings('ignore')

In [4]:
def load_data(data_file):
    '''Takes in a file name. Returns a 
    dataframe of the unpacked file.'''
    
    # Open the tracking data. 
    with open(data_file, encoding="utf8") as f:
        lines = f.read().splitlines()
    # Create the dataframe.
    df = pd.DataFrame(lines)
    df.columns = ['json_data']
    unpacked_tracking_df = pd.io.json.json_normalize(df.json_data.apply(json.loads))

    return unpacked_tracking_df
        

In [5]:
def unpack_loc_data(df, loc_col, team):
    '''Takes in a dataframe, the column with the location data, and 
    whether the team was home or away. Unpacks the tracking data 
    into 3 columns per player in each row with each column being 
    the x, y, or z position. Returns a list of the player Ids.'''
    
#     players = []
    for player in loc_col:
        df[team + '_' + player['playerId'] + '_loc'] = (player['xyz'][0], player['xyz'][1])
#         df[team + '_' + player['playerId'] + '_y'] = player['xyz'][1]
#         df[team + '_' + player['playerId'] + '_z'] = player['xyz'][2]
#         players.append(player['playerId'])
        
    return None

In [6]:
def get_player_coords(event_tracking_df):
    '''Takes in the dataframe. Returns the x, y coordinates for the 
    home players and the away players.'''
    
    home_coords = {}
    print(event_tracking_df['home_ids'])
    for player in event_tracking_df['home_ids']: 
        print(player)
        home_coords[player] = (event_tracking_df['home_' + player + '_x'][idx],
                               event_tracking_df['home_' + player + '_y'][idx])

    opposing_coords = {}
    for player in event_tracking_df['home_ids']:
        opposing_coords[player] = (event_tracking_df['away_' + player + '_x'][idx], 
                                   event_tracking_df['away_' + player + '_y'][idx])
    
    return home_coords, opposing_coords

In [7]:
# def get_dist_closest():
#     '''Takes in one player's x and y coordinates and the the 
#     coordinates from all players on the opposing team. Returns 
#     the distance of the closest opposing player.'''
    
#     min_dist = 999999
#     for home_player in home_cords:
        
#     in opposing_coords:
#         curr_dist = math.dist([player_x, player_y], [opp_player[0], opp_player[1]])
        
#         if curr_dist < min_dist:
#             min_dist = curr_dist
        
#     return min_dist

In [8]:
def clean_game(event_tracking_df):
    '''Takes in the combined tracking and events dataframe for one game.
    Returns a dataframe with the columns unpacked, the cumulative fouls per
    player per game, and the distance between each player and the next 
    closest player at each data capture. Also returns the player lists from
    the unpack_loc_data call.'''
    
    # Get a list of players who committed at least one foul.
    players_fouled = event_tracking_df[event_tracking_df['eventType'] == 'FOUL']['playerId'].unique()
    
    # For each player who committed a foul, create a column to get their cumulative fouls in the game.
    for player in players_fouled:
        event_tracking_df['num_fouls_' + player] = np.where((event_tracking_df['eventType'] == 'FOUL') & \
                                                            (event_tracking_df['playerId'] == player),
                                                            1,
                                                            0)
        event_tracking_df['num_fouls_' + player] = event_tracking_df['num_fouls_' + player].cumsum()
    
    # Unpack the tracking data columns with unpack_loc_data.
    
    list_dicts = []
    for row in event_tracking_df['homePlayers_x']:
        row_dict = {}
        for test in row:
            row_dict[test['playerId']] = (test['xyz'][0], test['xyz'][1])
        list_dicts.append(row_dict)
        
    event_tracking_df['home_dict_loc'] = list_dicts
    
    list_dicts = []
    for row in event_tracking_df['awayPlayers_x']:
        row_dict = {}
        for test in row:
            row_dict[test['playerId']] = (test['xyz'][0], test['xyz'][1])
        list_dicts.append(row_dict)
        
    event_tracking_df['away_dict_loc'] = list_dicts
            
#         for player in row:
#             event_tracking_df['hom_' + player['playerId'] + '_loc'] = (player['xyz'][0], player['xyz'][1])
    
#     event_tracking_df['homePlayers_x'].apply(lambda x: unpack_loc_data(event_tracking_df, 
#                                                                       x,
#                                                                       'home'))
#     event_tracking_df['awayPlayers_x'].apply(lambda x: unpack_loc_data(event_tracking_df, 
#                                                                       x,
#                                                                       'away'))
    
    return event_tracking_df

    event_tracking_df['home_ids'] = event_tracking_df['homePlayers_x'].apply(unpack_loc_data, args='home')
    event_tracking_df['away_ids'] = event_tracking_df['homePlayers_x'].apply(unpack_loc_data, args='away')
    
    # Get the x and y coordinates for the home and away teams.
    event_tracking_df['home_coords'], event_tracking_df['opposing_coords'] = get_player_coords(event_tracking_df)
#     home_pl_ids = [player[0] for player in home_players]
#     print(home_players)
    # Get the minimum distance for each home player to an opposing player at each location capture.
#     for player, id_ in zip(home_coords, :
#         print(player)
#         event_tracking_df['min_dist_' + player] = get_dist_closest(player[0], player[1], opposing_coords)
    
    
    return event_tracking_df #, home_players, away_players

In [9]:
# Load the tracking data into a dataframe.
tracking_data = load_data(f"0042100301_tracking.jsonl")

In [10]:
# Load the play by play data into a dataframe.
events_data = load_data(f"0042100301_events.jsonl")

In [11]:
# Combine the tracking and events dataframes into one dataframe.
event_tracking_df = pd.merge(tracking_data, events_data, 
                             on=['shotClock', 'gameClock', 'wallClock'], 
                             how='inner')

In [12]:
df = clean_game(event_tracking_df)

In [43]:
def get_min_dict(col1, col2):
    dist_dict = {}
    min_dist = 9999999
    
    for x in col1.items():
        for test in x[1].items():
#             print(test)

            for y in col2.items():
#                 print(y[1].items())
                for test2 in y[1].items():
#                     print(test2)
                    print(test[1][0], test[1][1])
                    print(test2[1][0], test2[1][1])
                    curr_val = math.dist([test[1][0], test[1][1]], 
                                         [test2[1][0], test2[1][1]])
#                 print(curr_val)
                    if curr_val < min_dist:
                        min_dist = curr_val
#             print('*', min_dist)

        dist_dict[x[0]] = min_dist
        min_dist = 999999
    return dist_dict

In [ ]:
df['min_dist'] = df.apply(lambda x: get_min_dict(df['home_dict_loc'], df['away_dict_loc']))

2.22 -0.23
-1.29 -8.69
2.22 -0.23
-12.04 0.28
2.22 -0.23
-0.73 -2.43
2.22 -0.23
-2.14 7.16
2.22 -0.23
-19.73 -1.1
2.22 -0.23
-1.29 -8.69
2.22 -0.23
-12.04 0.28
2.22 -0.23
-0.73 -2.43
2.22 -0.23
-2.14 7.16
2.22 -0.23
-19.73 -1.1
2.22 -0.23
3.81 -10.99
2.22 -0.23
-11.64 0.91
2.22 -0.23
3.13 -4.81
2.22 -0.23
-7.23 6.59
2.22 -0.23
-18.3 -1.95
2.22 -0.23
32.45 -21.73
2.22 -0.23
2.74 2.41
2.22 -0.23
28.95 -2.36
2.22 -0.23
-4.34 -4.67
2.22 -0.23
2.91 -13.39
2.22 -0.23
45.6 -23.03
2.22 -0.23
14.64 2.11
2.22 -0.23
39.94 8.02
2.22 -0.23
12.74 -9.61
2.22 -0.23
12.12 -14.76
2.22 -0.23
28.58 -18.66
2.22 -0.23
35.91 23.58
2.22 -0.23
20.46 -10.57
2.22 -0.23
27.57 -10.09
2.22 -0.23
40.26 19.92
2.22 -0.23
21.39 -12.43
2.22 -0.23
26.55 20.22
2.22 -0.23
41 -7.28
2.22 -0.23
29.85 -22.33
2.22 -0.23
42.18 23.17
2.22 -0.23
33.89 -0.87
2.22 -0.23
27.56 21.92
2.22 -0.23
40.37 -4.55
2.22 -0.23
39.25 -23.42
2.22 -0.23
40.5 22.99
2.22 -0.23
14.05 3.69
2.22 -0.23
23.4 15.54
2.22 -0.23
37.79 -2.16
2.22 -0.23
22.23 

7.69 5.27
2.22 -0.23
-7.96 0.23
2.22 -0.23
-22.53 1.38
2.22 -0.23
-16.8 -1.83
2.22 -0.23
-11.78 -13.73
2.22 -0.23
0.85 7.45
2.22 -0.23
-15.26 -2.08
2.22 -0.23
-25.11 1.94
2.22 -0.23
-20.73 6.78
2.22 -0.23
-23.1 -13.17
2.22 -0.23
-37.38 7.05
2.22 -0.23
-39.8 -6.75
2.22 -0.23
-24.05 7.47
2.22 -0.23
-22.59 15.02
2.22 -0.23
-40.24 -18.81
2.22 -0.23
-38.88 15.67
2.22 -0.23
-42.46 -6.45
2.22 -0.23
-30.73 3.11
2.22 -0.23
-22.15 5.11
2.22 -0.23
-34.95 -15.81
2.22 -0.23
-39.11 15.38
2.22 -0.23
-44.23 -6.55
2.22 -0.23
-32.05 3.3
2.22 -0.23
-28.38 -2.43
2.22 -0.23
-34.52 -15.85
2.22 -0.23
-23 25.92
2.22 -0.23
-18.56 -4.16
2.22 -0.23
14.55 0.65
2.22 -0.23
-2.54 -0.93
2.22 -0.23
13.39 -22.31
2.22 -0.23
-20.42 25.72
2.22 -0.23
-20.54 -4.25
2.22 -0.23
15.62 -0.58
2.22 -0.23
0.73 4.22
2.22 -0.23
17.52 -22.51
2.22 -0.23
-15.38 23.12
2.22 -0.23
-19.27 -6.45
2.22 -0.23
15.9 -2.23
2.22 -0.23
4.31 10.07
2.22 -0.23
23.19 -22.7
2.22 -0.23
-2.27 19.19
2.22 -0.23
-0.74 -13.48
2.22 -0.23
14.24 -1.74
2.22 -0.23


28.25 16.86
2.22 -0.23
12.5 -12.25
2.22 -0.23
19.23 12.7
2.22 -0.23
14.2 -0.53
2.22 -0.23
4.23 3.6
2.22 -0.23
-18.69 17.96
2.22 -0.23
-6.5 -6.2
2.22 -0.23
-12.08 1.91
2.22 -0.23
-30.05 8.04
2.22 -0.23
-4.61 -7.13
2.22 -0.23
-37.21 13.34
2.22 -0.23
-27.99 -11.33
2.22 -0.23
-24.9 6.17
2.22 -0.23
-39.9 -3.62
2.22 -0.23
-8.92 -0.89
2.22 -0.23
-20.92 7.66
2.22 -0.23
-42.54 0.12
2.22 -0.23
-38.05 7.57
2.22 -0.23
-34.28 -7.01
2.22 -0.23
-25.22 -16.25
2.22 -0.23
-7.95 16.82
2.22 -0.23
-20.1 7.72
2.22 -0.23
-29.26 12.87
2.22 -0.23
-30.72 -2.86
2.22 -0.23
-37.39 4.08
2.22 -0.23
2.07 19.72
2.22 -0.23
-10.72 -0.41
2.22 -0.23
-22.21 14.81
2.22 -0.23
-22.14 -4.65
2.22 -0.23
-31.23 4.18
2.22 -0.23
-25.75 8.42
2.22 -0.23
-5.11 -18.96
2.22 -0.23
-29.69 3.44
2.22 -0.23
-28.7 -2.57
2.22 -0.23
-11.65 6.15
2.22 -0.23
-25.74 8.42
2.22 -0.23
-7.36 -18.24
2.22 -0.23
-31.57 4.37
2.22 -0.23
-29.09 -3.15
2.22 -0.23
-11.59 4.7
2.22 -0.23
-25.46 8.42
2.22 -0.23
-11.09 -17.16
2.22 -0.23
-33.86 6.01
2.22 -0.23
-29.7

15.34 6
2.22 -0.23
28.29 -11.61
2.22 -0.23
4.43 12.71
2.22 -0.23
25.06 1.7
2.22 -0.23
2.84 -14.32
2.22 -0.23
14.31 6.06
2.22 -0.23
27.19 -11.54
2.22 -0.23
3.49 12.67
2.22 -0.23
23.88 1.28
2.22 -0.23
2.09 -14.37
2.22 -0.23
6.9 5.12
2.22 -0.23
17.66 -11.25
2.22 -0.23
-3.37 12.18
2.22 -0.23
14.83 -2.43
2.22 -0.23
-3.83 -14.59
2.22 -0.23
-38.53 -2.14
2.22 -0.23
-39.36 8.25
2.22 -0.23
-36.4 3.15
2.22 -0.23
-35.71 -5.78
2.22 -0.23
-31.7 17.03
2.22 -0.23
-38.53 -2.14
2.22 -0.23
-39.36 8.25
2.22 -0.23
-36.4 3.15
2.22 -0.23
-35.71 -5.78
2.22 -0.23
-31.7 17.03
2.22 -0.23
-13.54 -5.94
2.22 -0.23
10.99 20.62
2.22 -0.23
8.85 -22.25
2.22 -0.23
-5.79 -6.39
2.22 -0.23
-4.64 20.92
2.22 -0.23
-3.38 -6.02
2.22 -0.23
29.57 18.55
2.22 -0.23
25.15 -24.06
2.22 -0.23
5.11 -4.24
2.22 -0.23
5.38 20.13
2.22 -0.23
16.66 -11.43
2.22 -0.23
41.58 18.42
2.22 -0.23
43.64 -15.04
2.22 -0.23
31.68 -2.46
2.22 -0.23
17.15 15.84
2.22 -0.23
-17.43 -6.7
2.22 -0.23
-24.62 14.42
2.22 -0.23
-17.08 -5.24
2.22 -0.23
-7.42 4.7
2.22

-1.58 -11.52
2.22 -0.23
-11.25 13.52
2.22 -0.23
-24.15 0.64
2.22 -0.23
-17.54 -2.36
2.22 -0.23
-17.65 -7.61
2.22 -0.23
-29.9 -12.25
2.22 -0.23
-21.27 18.25
2.22 -0.23
-32.6 12.13
2.22 -0.23
-33.81 -5.37
2.22 -0.23
-24.2 -6.78
2.22 -0.23
-39.22 -11.23
2.22 -0.23
-37.15 17.57
2.22 -0.23
-38.25 11.02
2.22 -0.23
-35.42 1.04
2.22 -0.23
-27.05 -8.28
2.22 -0.23
-40.94 -12.05
2.22 -0.23
-42.52 10.09
2.22 -0.23
-40.74 5.77
2.22 -0.23
-39.33 -0.51
2.22 -0.23
-28.19 -6.3
2.22 -0.23
-40.19 -12.42
2.22 -0.23
-43.7 7.48
2.22 -0.23
-36.44 4.48
2.22 -0.23
-40.33 -1.83
2.22 -0.23
-28.39 -0.06
2.22 -0.23
-38.32 -12.46
2.22 -0.23
-35.59 -1.54
2.22 -0.23
-18.33 1.33
2.22 -0.23
-47.23 -1.14
2.22 -0.23
-13.79 14.99
2.22 -0.23
-37.58 -12.24
2.22 -0.23
-33.98 -3.47
2.22 -0.23
-15.38 0.38
2.22 -0.23
-47.6 -1.81
2.22 -0.23
-11.51 16.19
2.22 -0.23
0.57 -4.22
2.22 -0.23
18.28 -21.48
2.22 -0.23
38.89 -16.14
2.22 -0.23
-3.84 7.02
2.22 -0.23
26.17 23.64
2.22 -0.23
6.07 -4.43
2.22 -0.23
17.83 -18.01
2.22 -0.23
28.14 

...

28.25 -0.25
25.69 6.75
-2.41 -6.9
25.69 6.75
37.25 9.62
25.69 6.75
38.04 -7.41
25.69 6.75
4.11 5.71
25.69 6.75
27.14 -0.23
25.69 6.75
-7.16 -6.99
25.69 6.75
31.29 5.01
25.69 6.75
27 -5.42
25.69 6.75
-0.07 6.3
25.69 6.75
22.68 -0.26
25.69 6.75
-10.17 -7.58
25.69 6.75
23.89 2.84
25.69 6.75
16.93 -3.95
25.69 6.75
-3.64 7.08
25.69 6.75
17.96 0.1
25.69 6.75
-10.39 -7.6
25.69 6.75
23.04 2.73
25.69 6.75
16.01 -3.8
25.69 6.75
-4.01 7.1
25.69 6.75
17.57 0.18
25.69 6.75
-29.85 -13.3
25.69 6.75
-12.93 -2.93
25.69 6.75
-18.75 -1.81
25.69 6.75
-21.27 11.25
25.69 6.75
1.54 3.41
25.69 6.75
-40.75 -14.8
25.69 6.75
-19.82 8.19
25.69 6.75
-21.37 -7.15
25.69 6.75
-41.34 15.59
25.69 6.75
-10.59 1.55
25.69 6.75
-40.31 -15.46
25.69 6.75
-31.06 6.12
25.69 6.75
-17.48 -9.82
25.69 6.75
-40.43 15.07
25.69 6.75
-14.9 -2.03
25.69 6.75
-39.3 -16.25
25.69 6.75
-36.15 2.38
25.69 6.75
-18.75 -12.27
25.69 6.75
-38.99 15.26
25.69 6.75
-15.94 -8.09
25.69 6.75
-41.61 -10.21
25.69 6.75
-32.7 -5.13
25.69 6.75
-39.34 11.92


-45.77 -8.45
25.69 6.75
-16.11 9.7
25.69 6.75
-27.92 10.44
25.69 6.75
24.89 18.17
25.69 6.75
-12.59 -4.76
25.69 6.75
-24.26 -4.81
25.69 6.75
18.05 -12.71
25.69 6.75
-5.58 7.86
25.69 6.75
42.65 24.01
25.69 6.75
8.13 -2.41
25.69 6.75
8.82 -7.83
25.69 6.75
19.02 -14.3
25.69 6.75
6.31 8.25
25.69 6.75
39.52 23.15
25.69 6.75
18.1 -5.84
25.69 6.75
21.13 -13.64
25.69 6.75
30.63 4.82
25.69 6.75
19.41 -1.17
25.69 6.75
38.75 22.75
25.69 6.75
16.31 -9.94
25.69 6.75
38.59 -23.58
25.69 6.75
42.35 6.91
25.69 6.75
28.55 -13.35
25.69 6.75
34.33 22.12
25.69 6.75
29.35 -0.38
25.69 6.75
36.91 -23.14
25.69 6.75
41.19 13.41
25.69 6.75
36.25 -7.72
25.69 6.75
27.86 19.77
25.69 6.75
34.91 2.24
25.69 6.75
36.91 -23.25
25.69 6.75
41.19 13.41
25.69 6.75
36.25 -7.72
25.69 6.75
27.86 19.77
25.69 6.75
34.91 2.24
25.69 6.75
36.91 -23.25
25.69 6.75
35.89 17.19
25.69 6.75
37.37 -4.2
25.69 6.75
9.11 12.19
25.69 6.75
34.38 4.27
25.69 6.75
27.76 -22.16
25.69 6.75
14.45 22.77
25.69 6.75
-11.74 6.03
25.69 6.75
-17.51 -14.71

25.69 6.75
-37.4 1.64
25.69 6.75
-7.01 -15.95
25.69 6.75
-22.51 3.31
25.69 6.75
-44.48 0.1
25.69 6.75
-9.9 7.27
25.69 6.75
-38.72 4.44
25.69 6.75
15.4 6.83
25.69 6.75
41.03 23.55
25.69 6.75
23.11 -0.43
25.69 6.75
31.43 -10.97
25.69 6.75
31.21 -23.16
25.69 6.75
7.41 7.55
25.69 6.75
26.62 18.27
25.69 6.75
16.49 -2.72
25.69 6.75
38.87 1.75
25.69 6.75
24.06 -19.35
25.69 6.75
2.8 6.3
25.69 6.75
22.93 15.54
25.69 6.75
10.47 -2.63
25.69 6.75
33.1 2.46
25.69 6.75
19.71 -17.57
25.69 6.75
-2.45 6.13
25.69 6.75
17.78 12.93
25.69 6.75
3.93 -3.05
25.69 6.75
24.81 1.73
25.69 6.75
15.62 -15.27
25.69 6.75
-3.35 6.16
25.69 6.75
17.02 12.72
25.69 6.75
3.05 -3.14
25.69 6.75
23.63 1.61
25.69 6.75
15.09 -14.95
25.69 6.75
-3.8 6.18
25.69 6.75
16.63 12.61
25.69 6.75
2.61 -3.18
25.69 6.75
23.03 1.55
25.69 6.75
14.83 -14.81
25.69 6.75
-28.77 -2.85
25.69 6.75
-39.37 13.76
25.69 6.75
-41.17 -3.55
25.69 6.75
-41.75 0.97
25.69 6.75
-38.34 -11.84
25.69 6.75
-23.09 0.45
25.69 6.75
-22.67 10.56
25.69 6.75
-41.5 -5.87

-26.91 9.51
25.69 6.75
-28.56 5.59
25.69 6.75
-40.32 7.61
25.69 6.75
-36.98 -2.18
25.69 6.75
-40.39 2.13
25.69 6.75
-27.81 9.58
25.69 6.75
-35.25 15.45
25.69 6.75
-31.5 8.81
25.69 6.75
-30.57 -11.22
25.69 6.75
-47.66 -0.48
25.69 6.75
-17.8 10.97
25.69 6.75
-35.41 15.98
25.69 6.75
-28.8 7.12
25.69 6.75
-28.21 -12.92
25.69 6.75
-46.95 -0.83
25.69 6.75
-15.1 11.48
25.69 6.75
-28.78 16.4
25.69 6.75
-13.12 -8.21
25.69 6.75
-3.59 -20.07
25.69 6.75
-23.08 -3.2
25.69 6.75
9.8 16.35
25.69 6.75
-22.85 15.55
25.69 6.75
-5.5 -13.46
25.69 6.75
9.12 -21.71
25.69 6.75
-9.13 -4.63
25.69 6.75
21.85 19.23
25.69 6.75
-15.96 14.47
25.69 6.75
2.03 -17.18
25.69 6.75
20.52 -22.25
25.69 6.75
7.03 -6.85
25.69 6.75
32.49 21.7
25.69 6.75
-8.71 13.17
25.69 6.75
8.89 -16.98
25.69 6.75
28.54 -22.64
25.69 6.75
23.13 -8.57
25.69 6.75
39.72 22.42
25.69 6.75
-1.43 11
25.69 6.75
15.79 -13.58
25.69 6.75
34.41 -22.75
25.69 6.75
36.65 -10.66
25.69 6.75
43.59 23.7
25.69 6.75
5.19 6.7
25.69 6.75
20.03 -5.67
25.69 6.75
38.42 

25.69 6.75
22.03 3.29
25.69 6.75
27.41 3.14
25.69 6.75
-31.52 8.58
25.69 6.75
31.15 -3.52
25.69 6.75
15.09 9.65
25.69 6.75
-35.49 0.33
25.69 6.75
12.06 3.14
25.69 6.75
-16.52 -8.06
25.69 6.75
-37.92 7.41
25.69 6.75
-37.94 -8.12
25.69 6.75
-26.76 0.58
25.69 6.75
15.75 2.75
25.69 6.75
-16.42 -7.75
25.69 6.75
-36.92 7.92
25.69 6.75
-36.42 -6.75
25.69 6.75
-26.58 0.75
25.69 6.75
40.4 6.75
25.69 6.75
-17.42 -6.55
25.69 6.75
-37.52 7.67
25.69 6.75
-37.15 -7.23
25.69 6.75
-26.93 0.58
25.69 6.75
41.04 6.72
25.69 6.75
-16.51 -5.88
25.69 6.75
-32.6 6.43
25.69 6.75
-30.11 -4.13
25.69 6.75
-27.3 0.61
25.69 6.75
38.65 5.2
25.69 6.75
-10.23 -4.7
25.69 6.75
-12.98 3.51
25.69 6.75
-10.71 -0.57
25.69 6.75
-16.84 -0.04
25.69 6.75
38.66 5.3
25.69 6.75
-9.83 -4.46
25.69 6.75
-11.81 3.34
25.69 6.75
-9.62 -0.52
25.69 6.75
-15.63 0.12
25.69 6.75
40.57 6.21
25.69 6.75
-1.72 3.44
25.69 6.75
2.7 3.5
25.69 6.75
4.13 0.15
25.69 6.75
0.15 4.29
25.69 6.75
38.49 -5.72
25.69 6.75
23.9 11.71
25.69 6.75
20.19 1.78
25.6

In [ ]:
df

In [ ]:
test =df[[x for x in df.columns if ('num_fouls_' in x)] + ['min_dist']].reset_index()

In [ ]:
corr_df = test.merge(test.min_dist.dropna().apply(pd.Series).reset_index(), on='index', how='outer')

In [ ]:
corr_df.columns.tolist()

In [ ]:
num_fouls_cols = [x for x in corr_df.columns if ('num_fouls_' in x)]
matching_cols = [x[10:] for x in num_fouls_cols]
final_list = list(zip(num_fouls_cols, matching_cols))

In [ ]:
corr_dicts = {}
for pair in final_list:
    try:
        cor_ = corr_df[[pair[0], pair[1]]].corr()
        corr_dicts[pair[1]] = cor_[pair[0]][1]
        
            
    except:
        #didnt foul
        pass
pd.DataFrame.from_dict(corr_dicts, 
                       orient='index', 
                       columns=['Correlation']).reset_index().rename(columns={'index': 'PlayerId'})

## Proposed Solution / Recommendations
The solution proposed here is to use the code here to print out a foul number vs. expected effectiveness chart for coaches to quickly reference during the game. It would not require any in game analyses which they would not have time for, but instead would be a physical sheet the coaches would have prior to the game. It would be simple and clear to enable coaches to quickly understand the expected effectiveness of each player at different numbers of fouls (and in/out of foul trouble). They could factor this information into their decision of how long they should sit the player in foul trouble based on their expected effectiveness when in foul trouble and likelihood to foul again. They could have this chart for both their own team and the opposing team. Having the chart for the away team could provide insight as to which players on the opposing team are not as effective under foul trouble. 

## Difficulties and Challenges
One challenge in this project was determining when players were in foul trouble. This can be context dependent, so I discussed with friends and looked online to make my decisions. Changing these cutoffs may change the outcomes of this project, as the comparisons between the statistics in and out of foul trouble would change. 

The main challenge with this project was not having a lot of cases of players in foul trouble. The dataset was imbalanced because the majority of the time, players are not in foul trouble. I used oversampling in the model to account for this.

Additionally, behaviors during playoff games and regular season games may be different. Players on teams that do not make the playoffs may also have different trends in performance in and out of foul trouble. If this method is used, a new model should be developed to make better predictions on this type of data. 

A second major problem I faced was that I had planned the project with my team and with the expectation that I would have 3 people working on this with me. Unfortunately my team stopped responding to messages after our initial meeting, so I had to complete the project alone. Although this caused a time crunch, I did get to complete the project from start to finish which gave me the opportunity to learn about working with sports data at every stage of the process.

## Next Steps
I would like to run the code on more data. I would also like to actually build out the model instead of just creating the simple chart. I could also get the chart for the away team so the coach could take advantage of players who play differently in foul trouble.

The next step I would like to take with this project is to make the effectiveness measure more robust. I think the tracking data on the ball could be used to see how close players are getting to the ball/player with the ball on defense, how quickly players move, and whether they jump on defense when in foul trouble. These ideas may not pan out, but I think they have potential and I would love to explore them. Additionally, if I could get feedback from coaches, I think I could improve the foul number vs. expected effectiveness chart to design it in a way they find most useful. Finally, with more training data, I could improve the model.